In [1]:
from sklearn import datasets
from sklearn.impute import SimpleImputer
from datetime import datetime

import tensorflow as tf
import numpy as np
import pandas as pd

pd.set_option('display.max_columns', None)
pd.set_option('display.max_row', None)

In [2]:
#读取数据
train = pd.read_csv('data/jinnan_round1_train_20181227.csv')
mytest = pd.read_csv('data/jinnan_round1_testA_20181227.csv')

In [9]:
#返回时间差，单位分钟
def delta_time(data, t1, t2, format1='%H:%M:%S', format2='%H:%M:%S'):
    new_col = t1 + '-' + t2
    data[new_col] = (pd.to_datetime(data[t1], format=format1) - pd.to_datetime(data[t2],  format=format2)).dt.total_seconds()/60
    data.loc[data[new_col] < 0, new_col]  = data[data[new_col] < 0][new_col] + 24*60
    return data


#将时间区间字段分割为两列时间字段
def split_time(data, split_col):
    col1 = split_col + 'a'
    col2 = split_col + 'b'
    data[[col1, col2]] = data[split_col].str.split('-', expand=True)   
    data = data.drop([split_col], axis=1)

    for col in [col1, col2]:
        data = clearn_time(data, col)
    return data


#清洗时间字段
def clearn_time(data, col):
    data[col] = data[col].str.replace(';', ':')    
    data[col] = data[col].str.replace('分', '')
    data[col] = data[col].str.replace('；', ':')
    data[col] = data[col].str.replace('"', ':')
    data[col] = data[col].str.replace('::', ':')
    return data


#根据colm名称确定时间转换的format
def judge_format(time_col):
    if time_col[-1] in ['a', 'b']:
        myformat = '%H:%M'
    else:
        myformat = '%H:%M:%S'
    return myformat


#数据清洗
def clearn_data(data):
    #NAN值太多，直接删除列
    data = data.drop(['A2', 'A7', 'A8', 'B11'], axis=1)
    #fillna with mean value
    my_inputer = SimpleImputer(copy=False)
    data[['A1','A3','A4', 'A21', 'A23', 'B1', 'B2', 'B3', 'B8', 'B12', 'B13']] = my_inputer.fit_transform(data[['A1','A3','A4', 'A21', 'A23', 'B1', 'B2', 'B3', 'B8', 'B12', 'B13']])
    
    #原时间格式有误
    data.loc[314, 'A9'] = '23:00:00'
    #根据上下文时间猜测前后时间间隔均为一小时，不一定准确
    data.loc[1320, 'A11'] = '22:30:00'
    data.loc[1079, 'A11'] = '00:30:00'
    data.loc[998, 'A16'] = '12:00:00'
    #data.loc[538, 'A9] = 700
    data = data.drop([386, 538, 586, 1140])    
    
    for col in ['A20', 'A28', 'B4', 'B9', 'B10']:
        data = split_time(data, col)    
    
    data.loc[641, 'A20a'] = '18:00'
    data.loc[197, 'A20a'] = '18:00'
    data.loc[358, 'A20a'] = '18:00'
    data.loc[700, 'A26'] = '13:00:00'#根据前后时间猜
    data.loc[141, 'A28a'] = '14:00'
    data.loc[17, 'A28b'] = '00:00'
    data.loc[17, 'B4a'] = '00:00'
    data.loc[600, 'B4a'] = '19:05'
    data.loc[161, 'B4b'] = '17:00'
    data.loc[237, 'B4b'] = '16:00'
    
    time_cols = ['A5', 'A9', 'A11', 'A14', 'A16', 'A20a', 'A20b', 'A24', 'A26', 'A28a', 'A28b', 'B4a', 'B4b', 'B7', 'B9a', 'B9b', 'B10a', 'B10b']
    for i in range(len(time_cols) - 1):
        format1 = judge_format(time_cols[i+1])
        format2 = judge_format(time_cols[i])      
        data = delta_time(data, time_cols[i+1], time_cols[i], format1=format1, format2=format2)
        
       
    
    #data = delta_time(data, 'A9', 'A5')
    #data = delta_time(data, 'A14', 'A11')
    #data = delta_time(data, 'A16', 'A14')    
    #data = split_time(data, 'A20')
    
    #data['A20a'] = data['A20a'].str.replace(';', ':')
    #data['A20b'] = data['A20b'].str.replace(';', ':')
    #data['A20b'] = data['A20b'].str.replace('分', '')
    
    #data = delta_time(data, 'A20a', 'A16', format1='%H:%M', format2='%H:%M:%S')
    #data = delta_time(data, 'A20b', 'A20a', format1='%H:%M', format2='%H:%M')
    #data = delta_time(data, 'A24', 'A20b', format1='%H:%M:%S', format2='%H:%M')
    
    #data = delta_time(data, 'A26', 'A24')
    
    #data = split_time(data, 'A28')
    
    #data['A28a'] = data['A28a'].str.replace('；', ':')
    
    #data = delta_time(data, 'A28a', 'A26', format1='%H:%M', format2='%H:%M:%S')
    #data = delta_time(data, 'A28b', 'A28a', format1='%H:%M', format2='%H:%M')
    
    #data = split_time(data, 'B4')
    
    #data['B4a'] = data['B4a'].str.replace('"', ':')
    
    #data['B4a'] = data['B4a'].str.replace('；', ':')
    #data['B4a'] = data['B4a'].str.replace(';', ':')
    #data['B4b'] = data['B4b'].str.replace(';', ':')
    #data['B4b'] = data['B4b'].str.replace('；', ':')
    
    #data = delta_time(data, 'B4a', 'A28b', format1='%H:%M', format2='%H:%M')
    #data = delta_time(data, 'B4b', 'B4a', format1='%H:%M', format2='%H:%M')
    #data = delta_time(data, 'B7', 'B4b', format1='%H:%M:%S', format2='%H:%M')
    
    #data = split_time(data, 'B9')
    #data['B9a'] = data['B9a'].str.replace('；', ':')
    #data['B9a'] = data['B9a'].str.replace(';', ':')
    #data['B9b'] = data['B9b'].str.replace('::', ':')
    #data['B9b'] = data['B9b'].str.replace(';', ':')
    #data = delta_time(data, 'B9a', 'B7', format1='%H:%M', format2='%H:%M:%S')
    #data = delta_time(data, 'B9b', 'B9a', format1='%H:%M', format2='%H:%M')
    
    #data = split_time(data, 'B10')
    #data['B10a'] = data['B10a'].str.replace('::', ':')
    #data['B10a'] = data['B10a'].str.replace(';', ':')
    #data['B10a'] = data['B10a'].str.replace('；', ':')
    #data['B10b'] = data['B10b'].str.replace(';', ':')
    #data['B10b'] = data['B10b'].str.replace('；', ':')    
    #data = delta_time(data, 'B10a', 'B9b', format1='%H:%M', format2='%H:%M')
    #data = delta_time(data, 'B10b', 'B10a', format1='%H:%M', format2='%H:%M')
    return data


#特征工程
def make_feature(data):
    return data

In [10]:
clearn_train = clearn_data(train)
my_inputer = SimpleImputer(copy=False)
clearn_train[['A24-A20b', 'A26-A24', 'A28a-A26', 'B10a-B9b', 'B10b-B10a']] = my_inputer.fit_transform(clearn_train[['A24-A20b', 'A26-A24', 'A28a-A26', 'B10a-B9b', 'B10b-B10a']])

clearn_train

sample_id     A1         A3     A4        A5    A6        A9  A10  \
0     sample_1528  300.0  405.00000  700.0  13:30:00  38.0  15:30:00  100   
1     sample_1698  300.0  405.00000  700.0  14:00:00  29.0  16:00:00  101   
2      sample_639  300.0  405.00000  700.0  14:00:00  29.0  16:00:00  102   
3      sample_483  300.0  405.00000  700.0   1:30:00  38.0   3:00:00  100   
4      sample_617  300.0  405.00000  700.0  22:00:00  29.0   0:00:00  101   
5      sample_373  300.0  405.00000  700.0   2:00:00  39.0   3:30:00  100   
6      sample_577  300.0  405.00000  700.0   8:00:00  29.0  10:00:00  101   
7      sample_212  300.0  405.00000  700.0   6:00:00  29.0   8:00:00  101   
8      sample_521  300.0  405.00000  700.0  17:30:00  21.0  19:00:00  100   
9     sample_1026  300.0  405.00000  700.0  11:00:00  21.0  12:30:00  100   
10    sample_1743  300.0  405.00000  700.0  14:00:00  29.0  16:00:00  101   
11    sample_1493  300.0  405.00000  700.0  21:00:00  37.0  23:00:00  100   
12    sample_1613  300.0  405.00000  700.0  11:00:00  33.0  12:30:00  100   
13     sample_621  300.0  405.00000  700.0   6:00:00  29.0   8:00:00  102   
14    sample_1269  300.0  405.00000  700.0   6:00:00  29.0   8:00:00  101   
15    sample_1037  300.0  405.00000  700.0  21:00:00  21.0  22:30:00  100   
16    sample_1736  300.0  405.00000  700.0   6:00:00  29.0   8:00:00  102   
17      sample_97  300.0  405.00000  700.0  16:00:00  29.0  18:00:00  102   
18     sample_642  300.0  405.00000  700.0  14:00:00  29.0  16:00:00  101   
19     sample_179  300.0  405.00000  700.0  14:00:00  29.0  16:00:00  101   
20     sample_759  300.0  405.00000  700.0   4:30:00  27.0   6:30:00  102   
21     sample_812  300.0  405.00000  700.0   6:00:00  30.0   8:00:00  102   
22    sample_1395  300.0  405.00000  700.0  14:00:00  30.0  16:00:00  102   
23     sample_922  300.0  405.00000  700.0  19:30:00  38.0  21:00:00  100   
24     sample_514  300.0  405.00000  700.0  11:00:00  26.0  12:30:00  100   
25      sample_72  300.0  405.00000  700.0  22:00:00  30.0   0:00:00  101   
26    sample_1344  300.0  405.00000  700.0   6:00:00  30.0   8:00:00  102   
27     sample_582  300.0  405.00000  700.0   9:30:00  20.0  11:30:00  101   
28    sample_1002  300.0  405.00000  700.0  14:00:00  21.0  15:00:00  100   
29    sample_1079  300.0  405.00000  700.0   1:00:00  27.0   2:30:00  100   
30     sample_484  300.0  405.00000  700.0  11:00:00  21.0  12:30:00  100   
31    sample_1823  300.0  405.00000  700.0   6:00:00  29.0   8:00:00  102   
32    sample_1818  300.0  405.00000  700.0  14:00:00  29.0  16:00:00  102   
33     sample_457  300.0  405.00000  700.0  18:00:00  35.0  19:00:00  100   
34      sample_69  300.0  405.00000  700.0   2:00:00  18.0   3:00:00  100   
35     sample_997  300.0  405.00000  700.0  12:00:00  21.0  13:30:00  100   
36    sample_1004  300.0  405.00000  700.0   7:00:00  20.0   8:30:00  100   
37     sample_232  300.0  405.00000  700.0  14:00:00  29.0  16:00:00  101   
38    sample_1851  300.0  405.00000  700.0   6:00:00  29.0   8:00:00  102   
39    sample_1167  300.0  405.00000  700.0  22:00:00  20.0   0:00:00  101   
40     sample_433  300.0  405.00000  700.0  17:00:00  21.0  19:00:00  100   
41    sample_1612  300.0  405.00000  700.0   0:00:00  21.0   1:30:00  100   
42     sample_673  300.0  405.00000  700.0  22:00:00  29.0   0:00:00  101   
43    sample_1958  300.0  405.00000  700.0   6:00:00  29.0   8:00:00  102   
44    sample_1046  250.0  340.00000  590.0  10:00:00  22.0  11:30:00  100   
45     sample_732  300.0  405.00000  700.0   6:00:00  28.0   8:00:00  102   
46     sample_355  300.0  405.00000  700.0   7:00:00  38.0   8:30:00  100   
47     sample_568  300.0  405.00000  700.0   8:00:00  29.0  10:00:00  102   
48    sample_1531  300.0  405.00000  700.0  16:40:00  41.0  17:50:00  100   
49     sample_949  300.0  405.00000  700.0  10:00:00  23.0  11:00:00  100   
50    sample_1856  300.0  405.00000  700.0  22:00:00  29.0   0:00:00  102   
51  

In [50]:
mytest

sample_id   A1     A2     A3   A4              A5  A6        A7    A8  \
0    sample_1656  300    NaN  405.0  700         6:00:00  29       NaN   NaN   
1    sample_1548  300    NaN  405.0  700        12:30:00  39  12:50:00  80.0   
2     sample_769  300    NaN  405.0  700         6:00:00  80       NaN   NaN   
3    sample_1881  300    NaN  405.0  700        22:00:00  29       NaN   NaN   
4    sample_1807  300    NaN  405.0  700        22:00:00  30       NaN   NaN   
5     sample_145  300    NaN  405.0  700        14:00:00  29       NaN   NaN   
6    sample_1212  300    NaN  405.0  700         6:00:00  29       NaN   NaN   
7     sample_944  300    NaN  405.0  700        10:00:00  24       NaN   NaN   
8     sample_829  300    NaN  405.0  700        21:00:00  30       NaN   NaN   
9     sample_616  300    NaN  405.0  700        14:00:00  28       NaN   NaN   
10   sample_1690  300    NaN  405.0  700        14:00:00  29       NaN   NaN   
11    sample_114  300    NaN  405.0  700        14:00:00  29       NaN   NaN   
12    sample_185  300    NaN  405.0  700        14:00:00  29       NaN   NaN   
13   sample_1141  300    NaN  405.0  700         1:00:00  29       NaN   NaN   
14   sample_1460  300    NaN  405.0  700         2:00:00  30       NaN   NaN   
15   sample_1835  300    NaN  405.0  700         6:00:00  29       NaN   NaN   
16   sample_1539  300    NaN  405.0  700        18:30:00  80       NaN   NaN   
17    sample_598  300    NaN  405.0  700        21:00:00  22       NaN   NaN   
18   sample_1800  300    NaN  405.0  700        14:00:00  29       NaN   NaN   
19    sample_394  300    NaN  405.0  700        22:00:00  23       NaN   NaN   
20   sample_1146  300    NaN  405.0  700        18:00:00  29       NaN   NaN   
21    sample_149  300    NaN  405.0  700        22:00:00  29       NaN   NaN   
22   sample_1750  300    NaN  405.0  700        22:00:00  29       NaN   NaN   
23   sample_1977  300    NaN  405.0  700        14:00:00  30       NaN   NaN   
24   sample_1830  300    NaN  405.0  700        14:00:00  30       NaN   NaN   
25    sample_818  300    NaN  405.0  700         6:00:00  27       NaN   NaN   
26    sample_881  300    NaN  405.0  700        21:30:00  40  21:45:00  80.0   
27     sample_77  300    NaN  405.0  700        14:00:00  30       NaN   NaN   
28   sample_1240  300    NaN  405.0  700        14:00:00  29       NaN   NaN   
29    sample_309  300    NaN  405.0  700         0:00:00  21       NaN   NaN   
30     sample_90  300    NaN  405.0  700        22:00:00  30       NaN   NaN   
31   sample_1447  300    NaN  405.0  700         8:00:00  22       NaN   NaN   
32   sample_1584  300    NaN  405.0  700         2:00:00  20       NaN   NaN   
33     sample_23  300    NaN  405.0  700         5:00:00  24       NaN   NaN   
34   sample_1188  300    NaN  405.0  700         6:00:00  29       NaN   NaN   
35   sample_1461  300    NaN  405.0  700        10:45:00  65       NaN   NaN   
36   sample_1691  300    NaN  405.0  700        22:00:00  29       NaN   NaN   
37    sample_316  300    NaN  405.0  700        16:00:00  32  16:20:00  80.0   
38    sample_299  300  125.0    NaN  980        22:30:00  24       NaN   NaN   
39    sample_459  300    NaN  405.0  700        13:00:00  29       NaN   NaN   
40    sample_462  300    NaN  405.0  700        16:00:00  21       NaN   NaN   
41   sample_1730  300    NaN  405.0  700         6:00:00  29       NaN   NaN   
42    sample_689  300    NaN  405.0  700        14:00:00  30       NaN   NaN   
43   sample_1943  300    NaN  405.0  700         6:00:00  30       NaN   NaN   
44   sample_1043  200    NaN  270.0  470         8:00:00  26       NaN   NaN   
45    sample_919  300    NaN  405.0  700        18:00:00  38  18:10:00  80.0   
46   sample_1104  300    NaN  405.0  700        18:00:00  29       NaN   NaN   
47    sample_348  300    NaN  405.0  700        13:00:00  39  13:15:00  81.0   
48    sample_123  300    NaN  405.0  700         5:00:00  21       NaN   NaN   
49   sa

In [5]:
mytest.loc[86, 'A5'] = '22:00:00'

#NAN值太多，直接删除列
test = mytest.drop(['A2', 'A7', 'A8', 'B11'], axis=1)
#fillna with mean value
my_inputer = SimpleImputer(copy=False)
test[['A1','A3','A4', 'A21', 'A23', 'B1', 'B2', 'B3', 'B8', 'B12', 'B13']] = my_inputer.fit_transform(test[['A1','A3','A4', 'A21', 'A23', 'B1', 'B2', 'B3', 'B8', 'B12', 'B13']])
    
test = delta_time(test, 'A9', 'A5')
test = delta_time(test, 'A14', 'A11')
test = delta_time(test, 'A16', 'A14')

test = split_time(test, 'A20')
test.loc[641, 'A20a'] = '18:00'
test.loc[197, 'A20a'] = '18:00'
test.loc[358, 'A20a'] = '18:00'
test['A20a'] = test['A20a'].str.replace(';', ':')
test['A20b'] = test['A20b'].str.replace(';', ':')
test['A20b'] = test['A20b'].str.replace('分', '')

test = delta_time(test, 'A20a', 'A16', format1='%H:%M', format2='%H:%M:%S')
test = delta_time(test, 'A20b', 'A20a', format1='%H:%M', format2='%H:%M')
test = delta_time(test, 'A24', 'A20b', format1='%H:%M:%S', format2='%H:%M')
test.loc[700, 'A26'] = '13:00:00'#根据前后时间猜
test = delta_time(test, 'A26', 'A24')

test = split_time(test, 'A28')
test.loc[141, 'A28a'] = '14:00'
test['A28a'] = test['A28a'].str.replace('；', ':')
test['A28b'] = test['A28b'].str.replace('；', ':')
test.loc[17, 'A28b'] = '00:00'
test = delta_time(test, 'A28a', 'A26', format1='%H:%M', format2='%H:%M:%S')
test = delta_time(test, 'A28b', 'A28a', format1='%H:%M', format2='%H:%M')

test = split_time(test, 'B4')
test.loc[17, 'B4a'] = '00:00'
test['B4a'] = test['B4a'].str.replace('"', ':')
test.loc[600, 'B4a'] = '19:05'
test['B4a'] = test['B4a'].str.replace('；', ':')
test['B4a'] = test['B4a'].str.replace(';', ':')
test['B4b'] = test['B4b'].str.replace(';', ':')
test['B4b'] = test['B4b'].str.replace('；', ':')
test.loc[161, 'B4b'] = '17:00'
test.loc[237, 'B4b'] = '16:00'
test = delta_time(test, 'B4a', 'A28b', format1='%H:%M', format2='%H:%M')
test = delta_time(test, 'B4b', 'B4a', format1='%H:%M', format2='%H:%M')
test = delta_time(test, 'B7', 'B4b', format1='%H:%M:%S', format2='%H:%M')

test = split_time(test, 'B9')
test['B9a'] = test['B9a'].str.replace('；', ':')
test['B9a'] = test['B9a'].str.replace(';', ':')
test['B9b'] = test['B9b'].str.replace('::', ':')
test['B9b'] = test['B9b'].str.replace(';', ':')
test = delta_time(test, 'B9a', 'B7', format1='%H:%M', format2='%H:%M:%S')
test = delta_time(test, 'B9b', 'B9a', format1='%H:%M', format2='%H:%M')

test = split_time(test, 'B10')
test['B10a'] = test['B10a'].str.replace('::', ':')
test['B10a'] = test['B10a'].str.replace(';', ':')
test['B10a'] = test['B10a'].str.replace('；', ':')
test['B10b'] = test['B10b'].str.replace(';', ':')
test['B10b'] = test['B10b'].str.replace('；', ':')    
test = delta_time(test, 'B10a', 'B9b', format1='%H:%M', format2='%H:%M')
test = delta_time(test, 'B10b', 'B10a', format1='%H:%M', format2='%H:%M')

my_inputer = SimpleImputer(copy=False)
test[['A25','A27','A20a-A16', 'A20b-A20a', 'A24-A20b', 'B10a-B9b', 'B10b-B10a']] = my_inputer.fit_transform(test[['A25','A27','A20a-A16', 'A20b-A20a', 'A24-A20b', 'B10a-B9b', 'B10b-B10a']])
test = test.drop([641, 197, 358, 700, 600, 161, 237])

In [72]:
clearn_train.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1392 entries, 0 to 1395
Data columns (total 61 columns):
sample_id    1392 non-null object
A1           1392 non-null float64
A3           1392 non-null float64
A4           1392 non-null float64
A5           1392 non-null object
A6           1392 non-null float64
A9           1392 non-null object
A10          1392 non-null int64
A11          1392 non-null object
A12          1392 non-null int64
A13          1392 non-null float64
A14          1392 non-null object
A15          1392 non-null float64
A16          1392 non-null object
A17          1392 non-null float64
A18          1392 non-null float64
A19          1392 non-null int64
A21          1392 non-null float64
A22          1392 non-null float64
A23          1392 non-null float64
A24          1391 non-null object
A25          1392 non-null object
A26          1390 non-null object
A27          1392 non-null int64
B1           1392 non-null float64
B2           1392 non-null float64


In [6]:
my_inputer = SimpleImputer(copy=False)
clearn_train[['A24-A20b', 'A26-A24', 'A28a-A26', 'B10a-B9b', 'B10b-B10a']] = my_inputer.fit_transform(clearn_train[['A24-A20b', 'A26-A24', 'A28a-A26', 'B10a-B9b', 'B10b-B10a']])
#clearn_train = clearn_train.drop([641, 197, 358, 700, 600, 161, 237])

In [71]:
a = ((pd.to_datetime(clearn_train['B4b'], format='%H:%M') - pd.to_datetime(clearn_train['B7'],  format='%H:%M:%S')).dt.total_seconds()/60)
b = pd.to_datetime(clearn_train['B10b'], format='%H:%M')
c = clearn_train['A24'].value_counts()
d = train[train['A9'].notnull() == True]


In [10]:
clearn_train[clearn_train.notnull() == True]

sample_id     A1         A3     A4        A5    A6        A9  A10  \
0     sample_1528  300.0  405.00000  700.0  13:30:00  38.0  15:30:00  100   
1     sample_1698  300.0  405.00000  700.0  14:00:00  29.0  16:00:00  101   
2      sample_639  300.0  405.00000  700.0  14:00:00  29.0  16:00:00  102   
3      sample_483  300.0  405.00000  700.0   1:30:00  38.0   3:00:00  100   
4      sample_617  300.0  405.00000  700.0  22:00:00  29.0   0:00:00  101   
5      sample_373  300.0  405.00000  700.0   2:00:00  39.0   3:30:00  100   
6      sample_577  300.0  405.00000  700.0   8:00:00  29.0  10:00:00  101   
7      sample_212  300.0  405.00000  700.0   6:00:00  29.0   8:00:00  101   
8      sample_521  300.0  405.00000  700.0  17:30:00  21.0  19:00:00  100   
9     sample_1026  300.0  405.00000  700.0  11:00:00  21.0  12:30:00  100   
10    sample_1743  300.0  405.00000  700.0  14:00:00  29.0  16:00:00  101   
11    sample_1493  300.0  405.00000  700.0  21:00:00  37.0  23:00:00  100   
12    sample_1613  300.0  405.00000  700.0  11:00:00  33.0  12:30:00  100   
13     sample_621  300.0  405.00000  700.0   6:00:00  29.0   8:00:00  102   
14    sample_1269  300.0  405.00000  700.0   6:00:00  29.0   8:00:00  101   
15    sample_1037  300.0  405.00000  700.0  21:00:00  21.0  22:30:00  100   
16    sample_1736  300.0  405.00000  700.0   6:00:00  29.0   8:00:00  102   
17      sample_97  300.0  405.00000  700.0  16:00:00  29.0  18:00:00  102   
18     sample_642  300.0  405.00000  700.0  14:00:00  29.0  16:00:00  101   
19     sample_179  300.0  405.00000  700.0  14:00:00  29.0  16:00:00  101   
20     sample_759  300.0  405.00000  700.0   4:30:00  27.0   6:30:00  102   
21     sample_812  300.0  405.00000  700.0   6:00:00  30.0   8:00:00  102   
22    sample_1395  300.0  405.00000  700.0  14:00:00  30.0  16:00:00  102   
23     sample_922  300.0  405.00000  700.0  19:30:00  38.0  21:00:00  100   
24     sample_514  300.0  405.00000  700.0  11:00:00  26.0  12:30:00  100   
25      sample_72  300.0  405.00000  700.0  22:00:00  30.0   0:00:00  101   
26    sample_1344  300.0  405.00000  700.0   6:00:00  30.0   8:00:00  102   
27     sample_582  300.0  405.00000  700.0   9:30:00  20.0  11:30:00  101   
28    sample_1002  300.0  405.00000  700.0  14:00:00  21.0  15:00:00  100   
29    sample_1079  300.0  405.00000  700.0   1:00:00  27.0   2:30:00  100   
30     sample_484  300.0  405.00000  700.0  11:00:00  21.0  12:30:00  100   
31    sample_1823  300.0  405.00000  700.0   6:00:00  29.0   8:00:00  102   
32    sample_1818  300.0  405.00000  700.0  14:00:00  29.0  16:00:00  102   
33     sample_457  300.0  405.00000  700.0  18:00:00  35.0  19:00:00  100   
34      sample_69  300.0  405.00000  700.0   2:00:00  18.0   3:00:00  100   
35     sample_997  300.0  405.00000  700.0  12:00:00  21.0  13:30:00  100   
36    sample_1004  300.0  405.00000  700.0   7:00:00  20.0   8:30:00  100   
37     sample_232  300.0  405.00000  700.0  14:00:00  29.0  16:00:00  101   
38    sample_1851  300.0  405.00000  700.0   6:00:00  29.0   8:00:00  102   
39    sample_1167  300.0  405.00000  700.0  22:00:00  20.0   0:00:00  101   
40     sample_433  300.0  405.00000  700.0  17:00:00  21.0  19:00:00  100   
41    sample_1612  300.0  405.00000  700.0   0:00:00  21.0   1:30:00  100   
42     sample_673  300.0  405.00000  700.0  22:00:00  29.0   0:00:00  101   
43    sample_1958  300.0  405.00000  700.0   6:00:00  29.0   8:00:00  102   
44    sample_1046  250.0  340.00000  590.0  10:00:00  22.0  11:30:00  100   
45     sample_732  300.0  405.00000  700.0   6:00:00  28.0   8:00:00  102   
46     sample_355  300.0  405.00000  700.0   7:00:00  38.0   8:30:00  100   
47     sample_568  300.0  405.00000  700.0   8:00:00  29.0  10:00:00  102   
48    sample_1531  300.0  405.00000  700.0  16:40:00  41.0  17:50:00  100   
49     sample_949  300.0  405.00000  700.0  10:00:00  23.0  11:00:00  100   
50    sample_1856  300.0  405.00000  700.0  22:00:00  29.0   0:00:00  102   
51  

In [11]:
time_col = ['A5', 'A9', 'A11', 'A14', 'A16', 'A24', 'A26', 'B5', 'B7', 'A20a', 'A20b', 'A28a', 'A28b', 'B4a', 'B4b', 'B9a', 'B9b', 'B10a', 'B10b']
clearn_train.loc[1304, 'A25'] = 80
y_train = clearn_train['result']
x_train = clearn_train.drop(['result', 'sample_id'], axis=1).drop(time_col, axis=1)
x_test = test.drop(['sample_id'], axis=1).drop(time_col, axis=1)

In [ ]:
clearn_train

In [87]:
x = tf.placeholder(tf.float32, [None, 40])
y = tf.placeholder(tf.float32, [None, 1])

weights_L1 = tf.Variable(tf.random_normal([40,40]))
biases_L1 = tf.Variable(tf.random_normal([40,40]))
fx_L1 = tf.matmul(x,weights_L1) + biases_L1
L1 = tf.nn.tanh(fx_L1)

weights_L2 = tf.Variable(tf.random_normal([40,40]))
biases_L2 = tf.Variable(tf.random_normal([1,40]))
fx_L2 = tf.matmul(x,weights_L2) + biases_L2
prediction = tf.nn.tanh(fx_L2)

loss = tf.reduce_mean(tf.square(y - prediction))

train_step = tf.train.GradientDescentOptimizer(0.1).minimize(loss)

with tf.Session() as sess:
    sess.run(tf.global_variables_initializer())
    for _ in range(200):
        sess.run(train_step, feed_dict={x:x_train,y:y_train})
        
    prediction_y = sess.run(prediction, feed_dict={x:x_test})

ValueError: Cannot feed value of shape (1392,) for Tensor 'Placeholder_13:0', which has shape '(?, 1)'

In [12]:
from sklearn.linear_model import LinearRegression
# 定义线性回归模型
model = LinearRegression(fit_intercept=True, normalize=False, 
    copy_X=True, n_jobs=1)

linreg = LinearRegression()
linreg.fit(x_train, y_train)
y_pred = linreg.predict(x_test)

In [17]:
y_pred.shape

(150,)

In [25]:
my_result = pd.read_csv('data/jinnan_round1_submit_20181227.csv', header=None)

In [26]:
my_result

0     1
0    sample_1656  0.01
1    sample_1548  0.01
2     sample_769  0.01
3    sample_1881  0.01
4    sample_1807  0.01
5     sample_145  0.01
6    sample_1212  0.01
7     sample_944  0.01
8     sample_829  0.01
9     sample_616  0.01
10   sample_1690  0.01
11    sample_114  0.01
12    sample_185  0.01
13   sample_1141  0.01
14   sample_1460  0.01
15   sample_1835  0.01
16   sample_1539  0.01
17    sample_598  0.01
18   sample_1800  0.01
19    sample_394  0.01
20   sample_1146  0.01
21    sample_149  0.01
22   sample_1750  0.01
23   sample_1977  0.01
24   sample_1830  0.01
25    sample_818  0.01
26    sample_881  0.01
27     sample_77  0.01
28   sample_1240  0.01
29    sample_309  0.01
30     sample_90  0.01
31   sample_1447  0.01
32   sample_1584  0.01
33     sample_23  0.01
34   sample_1188  0.01
35   sample_1461  0.01
36   sample_1691  0.01
37    sample_316  0.01
38    sample_299  0.01
39    sample_459  0.01
40    sample_462  0.01
41   sample_1730  0.01
42    sample_689  0.01
43   sample_1943  0.01
44   sample_1043  0.01
45    sample_919  0.01
46   sample_1104  0.01
47    sample_348  0.01
48    sample_123  0.01
49   sample_1645  0.01
50   sample_1522  0.01
51   sample_1874  0.01
52    sample_295  0.01
53    sample_954  0.01
54   sample_1529  0.01
55    sample_722  0.01
56   sample_1703  0.01
57   sample_1524  0.01
58    sample_125  0.01
59   sample_1922  0.01
60   sample_1186  0.01
61    sample_938  0.01
62   sample_1744  0.01
63    sample_936  0.01
64   sample_1973  0.01
65    sample_157  0.01
66   sample_1003  0.01
67   sample_1407  0.01
68   sample_1057  0.01
69   sample_1783  0.01
70     sample_48  0.01
71    sample_263  0.01
72    sample_678  0.01
73    sample_882  0.01
74   sample_1688  0.01
75   sample_1361  0.01
76   sample_1802  0.01
77    sample_250  0.01
78    sample_323  0.01
79   sample_1514  0.01
80   sample_1545  0.01
81    sample_830  0.01
82   sample_1757  0.01
83    sample_917  0.01
84   sample_1728  0.01
85    sample_352  0.01
86   sample_1229  0.01
87    sample_619  0.01
88   sample_1138  0.01
89    sample_687  0.01
90    sample_966  0.01
91    sample_537  0.01
92    sample_867  0.01
93    sample_928  0.01
94    sample_520  0.01
95   sample_1338  0.01
96    sample_988  0.01
97    sample_899  0.01
98     sample_15  0.01
99   sample_1412  0.01
100  sample_1915  0.01
101  sample_1885  0.01
102  sample_1893  0.01
103   sample_688  0.01
104  sample_1664  0.01
105  sample_1667  0.01
106  sample_1516  0.01
107   sample_437  0.01
108   sample_203  0.01
109  sample_1389  0.01
110   sample_761  0.01
111  sample_1373  0.01
112   sample_558  0.01
113  sample_1710  0.01
114   sample_153  0.01
115   sample_934  0.01
116    sample_54  0.01
117  sample_1227  0.01
118    sample_53  0.01
119  sample_1110  0.01
120    sample_49  0.01
121   sample_474  0.01
122  sample_1716  0.01
123  sample_1169  0.01
124  sample_1925  0.01
125   sample_667  0.01
126   sample_176  0.01
127  sample_1908  0.01
128   sample_160  0.01
129    sample_35  0.01
130  sample_1403  0.01
131  sample_1806  0.01
132   sample_241  0.01
133  sample_1059  0.01
134   sample_746  0.01
135   sample_513  0.01
136  sample_1088  0.01
137  sample_1370  0.01
138   sample_523  0.01
139   sample_319  0.01
140  sample_1923  0.01
141  sample_1296  0.01
142  sample_1152  0.01
143   sample_982  0.01
144   sample_304  0.01
145   sample_502  0.01
146  sample_1951  0.01
147   sample_386  0.01
148   sample_362  0.01
149   sample_522  0.01

In [27]:
my_result[1] = y_pred

In [28]:
my_result

0         1
0    sample_1656  0.927448
1    sample_1548  0.899055
2     sample_769  0.935809
3    sample_1881  0.925015
4    sample_1807  0.928041
5     sample_145  0.925668
6    sample_1212  0.923863
7     sample_944  0.919226
8     sample_829  0.937864
9     sample_616  0.925385
10   sample_1690  0.939341
11    sample_114  0.939483
12    sample_185  0.956310
13   sample_1141  0.939557
14   sample_1460  0.905635
15   sample_1835  0.925668
16   sample_1539  0.913069
17    sample_598  0.932945
18   sample_1800  0.939121
19    sample_394  0.913871
20   sample_1146  0.925452
21    sample_149  0.940975
22   sample_1750  0.926675
23   sample_1977  0.952857
24   sample_1830  0.942257
25    sample_818  0.938323
26    sample_881  0.898812
27     sample_77  0.925938
28   sample_1240  0.943150
29    sample_309  0.902881
30     sample_90  0.941545
31   sample_1447  0.905624
32   sample_1584  0.914219
33     sample_23  0.910882
34   sample_1188  0.925232
35   sample_1461  0.903182
36   sample_1691  0.925015
37    sample_316  1.172259
38    sample_299  0.882672
39    sample_459  0.896791
40    sample_462  0.900617
41   sample_1730  0.938045
42    sample_689  0.941123
43   sample_1943  0.938642
44   sample_1043  0.898655
45    sample_919  0.933734
46   sample_1104  0.937875
47    sample_348  0.907028
48    sample_123  0.908919
49   sample_1645  0.925232
50   sample_1522  0.896578
51   sample_1874  0.927059
52    sample_295  0.886101
53    sample_954  0.921984
54   sample_1529  0.913990
55    sample_722  0.938572
56   sample_1703  0.925668
57   sample_1524  0.897702
58    sample_125  0.927070
59   sample_1922  0.938323
60   sample_1186  0.924385
61    sample_938  0.937679
62   sample_1744  0.925015
63    sample_936  0.912275
64   sample_1973  0.954072
65    sample_157  0.924184
66   sample_1003  0.892317
67   sample_1407  0.924687
68   sample_1057  0.925025
69   sample_1783  0.925668
70     sample_48  0.912693
71    sample_263  0.951906
72    sample_678  0.925366
73    sample_882  0.896469
74   sample_1688  0.927747
75   sample_1361  0.937864
76   sample_1802  0.927963
77    sample_250  0.927785
78    sample_323  0.904160
79   sample_1514  0.908752
80   sample_1545  0.910207
81    sample_830  0.939078
82   sample_1757  0.943954
83    sample_917  0.916739
84   sample_1728  0.927014
85    sample_352  0.909976
86   sample_1229  0.939557
87    sample_619  0.925124
88   sample_1138  0.939557
89    sample_687  0.925668
90    sample_966  0.913943
91    sample_537  0.895425
92    sample_867  0.910676
93    sample_928  0.934858
94    sample_520  0.924204
95   sample_1338  0.938939
96    sample_988  0.910209
97    sample_899  0.908583
98     sample_15  0.922889
99   sample_1412  0.922809
100  sample_1915  0.941559
101  sample_1885  0.939121
102  sample_1893  0.927295
103   sample_688  0.925668
104  sample_1664  0.939557
105  sample_1667  0.939013
106  sample_1516  0.908371
107   sample_437  0.901922
108   sample_203  0.925452
109  sample_1389  0.927938
110   sample_761  0.958149
111  sample_1373  0.939078
112   sample_558  0.939557
113  sample_1710  0.913262
114   sample_153  0.943194
115   sample_934  0.917138
116    sample_54  0.920991
117  sample_1227  0.927059
118    sample_53  0.893503
119  sample_1110  0.925452
120    sample_49  0.911882
121   sample_474  0.906779
122  sample_1716  0.913218
123  sample_1169  0.944464
124  sample_1925  0.938642
125   sample_667  0.928886
126   sample_176  0.955808
127  sample_1908  0.925232
128   sample_160  0.958284
129    sample_35  0.936560
130  sample_1403  0.953010
131  sample_1806  0.939809
132   sample_241  0.937864
133  sample_1059  0.926361
134   sample_746  0.943832
135   sample_513  0.924227
136  sample_1088  0.921938
137  sample_1370  0.938170
138   sample_523  0.924806
139   sample_319  0.898342
140  sample_1923  0.951470
141  sample_1296  0.956119
142  sample_1152  0.925015
143   sample_982  0.916569
144   sample_304  0.890863
145   sample_502  0.937447
146  sample_1951  0.939231
147   sample_386  0

In [31]:
my_result.to_csv('my_submit_20190112.csv', index=0, header=0)